# AE 370 Project 2 Song Notebook
### The damped wave equation of a string

This notebook focuses on the application of the string simulation. It uses real physical values to simulate a guitar string and creates a song using the method.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from moviepy.editor import ImageSequenceClip, AudioClip, VideoFileClip, concatenate_videoclips
from IPython.display import Audio, Video, display, clear_output
from ipywidgets import (
    FloatSlider, IntSlider, Dropdown, IntText, HTML,
    Button, HBox, VBox, Play, jslink, Output, Label
)
from scipy.linalg import solve_banded

In [ ]:
# Exact solution (only for sine wave ICs)
def u_exact(x, t, L, c, m, alpha):
    """
    Exact normal-mode solution of the damped 1D wave equation:

        u_tt + 2*alpha*u_t = c^2 u_xx

    with fixed ends. Underdamped case alpha < m*pi*c/L.
    """
    omega = m * np.pi * c / L             # natural frequency
    Omega = np.sqrt(omega**2 - alpha**2)  # damped frequency

    spatial = np.sin(m * np.pi * x / L)
    temporal = np.exp(-alpha * t) * np.cos(Omega * t)

    return spatial * temporal

# Default Parameters
class Parameters:
    L = 1.0 #m
    c = 504.9 #m/s
    T = 2.0 #s
    fs_audio = 44100
    N_target = 500
    ic_type = "pluck"
    pluck_pos = 0.2
    pluck_amplitude = 0.5
    velocity_pos = 0.2
    mode_number = 3
    pickup_pos = 0.1
    alpha = 3.0
parameters = Parameters()

In [ ]:
# MASTER MUSICAL CONFIG (RUN THIS AFTER EVERY RESTART)

# Tie the "song" settings directly to your Parameters object
c_base          = parameters.c          # wave speed (m/s)
fs_song         = parameters.fs_audio   # audio sample rate
N_target_song   = parameters.N_target   # spatial resolution
alpha_song      = parameters.alpha      # damping
pluck_pos_song  = parameters.pluck_pos  # pluck position (x/L)
pluck_amp_song  = parameters.pluck_amplitude
pickup_pos_song = parameters.pickup_pos

# Base frequency for scale degree 1
f1_base = 329.63  # Hz

# Major scale semitone offsets relative to degree 1
_semitone_offsets = {
    1: 0,
    2: 2,
    3: 4,
    4: 5,
    5: 7,
    6: 9,
    7: 11,
    8: 12,
}

def degree_to_freq(deg):
    """Map integer scale degree (1..8) to physical frequency in Hz."""
    return f1_base * 2.0 ** (_semitone_offsets[deg] / 12.0)

def freq_to_length(f, c=None):
    """
    Given desired fundamental frequency f (Hz),
    return string length L so that f = c/(2L).
    """
    if c is None:
        c = c_base
    return c / (2.0 * f)


In [ ]:
# Method

# Implicit trapezoidal finite-difference solve
def string_simulate(
    L=parameters.L,
    c=parameters.c,
    T=parameters.T,
    fs_audio=parameters.fs_audio,
    N_target=parameters.N_target,
    ic_type=parameters.ic_type,
    pluck_pos=parameters.pluck_pos,
    pluck_amplitude=parameters.pluck_amplitude,
    velocity_pos=parameters.velocity_pos,
    mode_number=parameters.mode_number,
    pickup_pos=parameters.pickup_pos,
    alpha=parameters.alpha,
):
    """
    1D string solver for

        u_tt + 2*alpha*u_t = c^2 u_xx,  0 < x < L

    with fixed ends u(0,t)=u(L,t)=0.

    Parameters
    ----------
    L : float
        String length.
    c : float
        Wave speed.
    T : float
        Total simulation time.
    fs_audio : int
        Audio sampling rate (sets dt = 1/fs_audio).
    N_target : int
        Target number of spatial intervals (may be reduced by CFL).
    ic_type : {"pluck", "mode", "velocity"}
        Type of initial displacement.
    pluck_pos : float
        Pluck position (fraction of length) if ic_type="pluck".
    pluck_amplitude : float
        Pluck amplitude if ic_type="pluck".
    mode_number : int
        Mode number if ic_type="mode".
    pickup_pos : float
        Position where we record the signal (fraction of length).
    alpha : float
        Damping coefficient in 1/s; 0 = undamped.

    Returns
    -------
    x : ndarray, shape (N+1,)
        Spatial grid.
    t_audio : ndarray
        Time samples.
    audio : ndarray
        Recorded displacement at pickup (normalized).
    snapshots : ndarray, shape (num_snapshots, N+1)
        Snapshots of u(x,t) over time.
    t_snap : ndarray
        Times corresponding to snapshots.
    """
    dt = 1.0 / fs_audio
    n_steps = int(T / dt)
    if n_steps < 3:
        raise ValueError("T too small for chosen fs_audio.")
    max_frames = int(30 * T)

    N = N_target

    # Spatial grid
    x = np.linspace(0.0, L, N + 1)
    dx = L / N

    # Initial conditions
    u = np.zeros_like(x)
    v = np.zeros_like(x)

    if ic_type == "pluck":
        xp = pluck_pos * L
        left = x <= xp
        right = x > xp
        if xp > 0:
            u[left] = x[left] / xp
        if L > xp:
            u[right] = (L - x[right]) / (L - xp)
        u *= pluck_amplitude
        # v stays zero
    elif ic_type == "mode":
        u = np.sin(mode_number * np.pi * x / L)
        # v stays zero
    elif ic_type == "velocity":
        # Zero displacement, localized initial velocity
        xv = velocity_pos * L
        jp_vel = int(round(xv / dx))
        jp_vel = max(1, min(N - 1, jp_vel))  # interior index

        amplitude = 0.5
        v[jp_vel] = amplitude
        if jp_vel > 0:
            v[jp_vel - 1] = amplitude * 0.5
        if jp_vel < N:
            v[jp_vel + 1] = amplitude * 0.5
    else:
        raise ValueError("ic_type must be 'pluck', 'mode', or 'velocity'")

    # Enforce 0 displacement BC at ends
    u[0] = u[-1] = 0.0
    v[0] = v[-1] = 0.0

    # Initial acceleration
    a = np.zeros_like(x)
    u_xx = np.zeros_like(x)
    u_xx[1:-1] = (u[2:] - 2.0*u[1:-1] + u[:-2]) / dx**2
    a[1:-1] = c**2 * u_xx[1:-1] - 2.0 * alpha * v[1:-1]

    lam = c * dt / dx
    gamma = lam**2  # c^2 dt^2 / dx^2
    M = N - 1     # number of interior points

    # Set up banded A matrix
    A = np.zeros((3, M))
    main_diag = (4.0 + 4.0 * alpha * dt + 2.0 * gamma) * np.ones(M)
    off_diag  = -gamma * np.ones(M - 1)
    A[0, 1:] = off_diag
    A[1, :] = main_diag
    A[2, :-1] = off_diag

    # Interior points
    u_int = u[1:-1].copy()
    v_int = v[1:-1].copy()
    a_int = a[1:-1].copy()

    # Pickup index
    jp = int(round(pickup_pos * L / dx))
    jp = max(1, min(N - 1, jp))

    # Audio buffer
    audio = np.zeros(n_steps)
    audio[0] = u[jp]

    # Snapshots (ensure final time is included)
    k_snapshots = max(n_steps // max_frames, 1)
    snapshots = [u.copy()]
    t_snap = [0.0]

    # Implicit time stepping trapezoid
    for n in range(n_steps - 1):
        rhs = (
            a_int * dt**2
            + 2.0 * alpha * dt * (dt * v_int + 2.0 * u_int)
            + 4.0 * dt * v_int
            + 4.0 * u_int
        )

        # Solve for interior nodes u^{n+1}
        u_int_next = solve_banded((1,1), A, rhs)

        # Fix ends
        u_next = np.zeros_like(u)
        u_next[1:-1] = u_int_next

        # Update acceleration
        a_int_next = (
            -a_int * dt**2 - 4.0 * dt * v_int - 4.0 * u_int + 4.0 * u_int_next
        ) / dt**2

        # Update velocity
        v_int_next = v_int + 0.5 * dt * (a_int + a_int_next)

        # Increment u
        u_int, v_int, a_int = u_int_next, v_int_next, a_int_next
        u[1:-1] = u_int
        v[1:-1] = v_int

        # Audio
        audio[n+1] = u[jp]

        # Snapshots
        if (n + 1) % k_snapshots == 0:
            snapshots.append(u.copy())
            t_snap.append((n+1)*dt)

    # Ensure final time snapshot is included
    final_t = (n_steps - 1) * dt
    if t_snap[-1] < final_t - 1e-12:
        snapshots.append(u.copy())
        t_snap.append(final_t)

    # Normalize audio
    max_val = np.max(np.abs(audio))
    if max_val > 0:
        audio /= max_val

    snapshots = np.vstack(snapshots)
    t_snap = np.array(t_snap)
    t_audio = np.linspace(0.0, dt*(n_steps-1), n_steps)

    return x, t_audio, audio, snapshots, t_snap

In [ ]:
# Visualization and interaction functions
figsize = (7, 3)
dpi = 100

def string_visualize(x, snapshots, t_snap):
    """
    Interactive plot using ipywidgets.
    """
    n_frames = snapshots.shape[0]
    y_min = -1.2
    y_max = 1.2

    out = Output()

    frame_slider = IntSlider(
        value=0,
        min=0,
        max=n_frames - 1,
        step=1,
        description="Frame",
        continuous_update=True,
        readout=True,
    )

    play = Play(
        value=0,
        min=0,
        max=n_frames - 1,
        step=1,
        interval=25,
        description="Play",
        disabled=False,
    )

    jslink((play, "value"), (frame_slider, "value"))

    def update_frame(k):
        with out:
            out.clear_output(wait=True)
            y = snapshots[k]
            if not np.all(np.isfinite(y)):
                print(f"Frame {k}: non-finite data, skipping plot.")
                return
            fig, ax = plt.subplots(figsize=figsize,dpi=dpi)
            ax.plot(x, y, lw=2)
            ax.set_xlabel("x (m)")
            ax.set_ylabel("Displacement")
            ax.set_title(f"t = {t_snap[k]:.4f} s")
            ax.xaxis.grid(False)
            ax.yaxis.grid(True)
            ax.set_ylim(y_min, y_max)
            display(fig)
            plt.close(fig)

    def on_value_change(change):
        update_frame(change["new"])

    frame_slider.observe(on_value_change, names="value")
    controls = HBox([play, frame_slider])
    display(VBox([controls, out]))
    update_frame(0)


# Video
def string_video(
    x,
    snapshots,
    t_snap,
    audio,
    fs_audio,
    filename="string_with_audio.mp4",
):
    """
    Create an MP4 video of the vibrating string with synchronized audio.

    Fix: we take the audio duration as ground truth and set
    fps = n_frames / duration_audio so that video_duration == audio_duration.
    """
    audio_np = audio.astype(np.float32)
    duration_audio = len(audio_np) / float(fs_audio)

    n_frames = snapshots.shape[0]
    if duration_audio <= 0 or n_frames < 2:
        raise ValueError("Not enough data to build a meaningful video.")

    # FPS chosen so that video covers exactly the audio duration
    fps = n_frames / duration_audio
    #print(f"Using fps = {fps:.2f}, audio duration = {duration_audio:.3f} s")

    # y-limits for consistent axis
    ymin = -1.2
    ymax = 1.2

    # Render frames
    frames = []
    for k in range(n_frames):
        # Map frame index to "video time" for title
        t_frame = (k / (n_frames - 1)) * duration_audio

        fig, ax = plt.subplots(figsize=figsize,dpi=dpi)
        ax.plot(x, snapshots[k], lw=2)
        ax.set_xlim(x[0], x[-1])
        ax.set_ylim(ymin, ymax)
        ax.set_xlabel("x (m)")
        ax.set_ylabel("Displacement")
        ax.set_title(f"t \u2248 {t_frame:.4f} s")
        ax.xaxis.grid(False)
        ax.yaxis.grid(True)
        fig.subplots_adjust(bottom=0.2)
        fig.canvas.draw()
        buf = fig.canvas.renderer.buffer_rgba()
        img_rgba = np.asarray(buf, dtype=np.uint8)
        img_rgb = img_rgba[..., :3]
        frames.append(img_rgb)
        plt.close(fig)

    # Build video clip; its duration will be n_frames / fps = duration_audio
    clip = ImageSequenceClip(frames, fps=fps)

    # Build audio clip
    def audio_func(t):
        t = np.array(t, dtype=float)
        idx = (t * fs_audio).astype(int)
        idx = np.clip(idx, 0, len(audio_np) - 1)
        return audio_np[idx]

    audio_clip = AudioClip(audio_func, duration=duration_audio, fps=fs_audio)
    clip = clip.set_audio(audio_clip)

    #print(f"Writing {filename} ...")
    clip.write_videofile(filename, fps=fps, codec="libx264", audio_codec="aac", verbose=False, logger=None)
    #print("Done.")
    return filename

# Interactive simulation
def string_interactive():
    """
    Interactive sliders for the simple damped string model,
    with buttons to run the simulation and generate a video with audio.
    """
    # Widgets
    L_w =               FloatSlider(value=parameters.L, min=0.5, max=2.0, step=0.1, description="L (m)")
    c_w =               FloatSlider(value=parameters.c, min=20.0, max=1000.0, step=10.0, description="c (m/s)")
    T_w =               FloatSlider(value=parameters.T, min=0.2, max=5.1, step=0.1, description="T (s)")
    alpha_w =           FloatSlider(value=parameters.alpha, min=0.0, max=10.0, step=0.1,description="alpha (damp)")
    pluck_pos_w =       FloatSlider(value=parameters.pluck_pos, min=0.05, max=0.95, step=0.05,description="Pluck x/L")
    pluck_amplitude_w = FloatSlider(value=parameters.pluck_amplitude, min=0.0, max=1.0, step=0.05,description="Pluck Amplitude")
    velocity_pos_w =    FloatSlider(value=parameters.velocity_pos, min=0.05, max=0.95, step=0.05,description="Velocity x/L")
    pickup_pos_w =      FloatSlider(value=parameters.pickup_pos, min=0.1, max=0.9, step=0.05,description="Pickup x/L")
    fs_w =              Dropdown(options=[8000, 16000, 22050, 44100, 96000],value=parameters.fs_audio, description="fs (Hz)")
    ic_w =              Dropdown(options=[("Pluck (Displacement IC)", "pluck"), ("Velocity pulse (Velocity IC)", "velocity"), ("Mode shape (Displacement IC)", "mode")],value=parameters.ic_type, description="IC")
    mode_n_w =          IntSlider(value=parameters.mode_number, min=1, max=10, step=1, description="Mode n")
    N_target_w =        IntSlider(value=parameters.N_target, min=50, max=1000, step=25,description="N")
    video_id_w =        IntText(value=1, description="Video #")

    run_btn = Button(description="Run simulation", button_style="primary")
    video_btn = Button(description="Generate video", button_style="success")

    sim_out = Output()
    video_out = Output()

    # State shared between run + video
    state = {"x": None, "snapshots": None, "t_snap": None,
             "audio": None, "fs": None}

    def on_run_clicked(b):
        with sim_out:
            clear_output(wait=True)
            try:
                print("Running simulation...")
                x, t_audio, audio, snapshots, t_snap = string_simulate(
                    L=L_w.value,
                    c=c_w.value,
                    T=T_w.value,
                    fs_audio=int(fs_w.value),
                    N_target=int(N_target_w.value),
                    ic_type=ic_w.value,
                    pluck_pos=pluck_pos_w.value,
                    pluck_amplitude=pluck_amplitude_w.value,
                    velocity_pos=velocity_pos_w.value,
                    mode_number=int(mode_n_w.value),
                    pickup_pos=pickup_pos_w.value,
                    alpha=alpha_w.value,
                    #max_frames=max_frames_calculated
                )
                dx = x[1] - x[0]
                dt = t_audio[1] - t_audio[0]
                print(f"Grid: N = {len(x)-1}, dx = {dx:.3e}, dt = {dt:.3e}")
                #print(f"Snapshots stored: {snapshots.shape[0]}")

                # Save for video
                state["x"] = x
                state["snapshots"] = snapshots
                state["t_snap"] = t_snap
                state["audio"] = audio
                state["fs"] = int(fs_w.value)

                string_visualize(x, snapshots, t_snap)
                print("Audio:")
                display(Audio(audio, rate=int(fs_w.value)))
            except Exception as e:
                print("Error during simulation:", e)

    def on_video_clicked(b):
        with video_out:
            clear_output(wait=True)
            if (state["x"] is None) or (state["snapshots"] is None):
                print("Run a simulation first.")
                return
            try:
                vid_name = f"string_with_audio_{video_id_w.value}.mp4"
                fname = string_video(
                    state["x"],
                    state["snapshots"],
                    state["t_snap"],
                    state["audio"],
                    state["fs"],
                    filename=vid_name,
                )
                print("Video:")
                display(Video(fname, embed=True))
            except Exception as e:
                print("Error generating video:", e)

    run_btn.on_click(on_run_clicked)
    video_btn.on_click(on_video_clicked)

    controls_box = VBox([
        HTML('<b>Physical Parameters</b>'),
        L_w, c_w, alpha_w, T_w,

        HTML('<b>Initial Conditions</b>'),
        ic_w, pluck_pos_w, pluck_amplitude_w,
        velocity_pos_w, mode_n_w, pickup_pos_w,

        HTML('<b>Simulation Parameters</b>'),
        fs_w, N_target_w,

        HTML('<b>Generate Simulation</b>'),
        run_btn,

        HTML('<b>Generate Video (Run Simulation First)</b>'),
        video_id_w, video_btn
    ])

    ui = VBox([
        controls_box,
        sim_out,
        video_out
    ])
    display(ui)

In [ ]:
# Helper: play melody with rests
def play_melody_with_rests(melody_degrees, melody_durations, name="melody_with_rests"):
    """
    Like the FFT/Mary note loop, but:
      - if degree is 0 or None, we insert a rest
        (silent segment) of the given duration instead of a note.
    Uses:
      - degree_to_freq(deg) for non-rests
      - freq_to_length(freq, c=c_base)
      - string_simulate(...) with pluck IC
    """
    assert len(melody_degrees) == len(melody_durations), \
        "degrees and durations must have same length"

    segments = []

    print(f"Generating '{name}' (with rests)...")
    print(f"{'Note':>4} {'deg':>4} {'type':>8} {'f_note [Hz]':>12} {'L_note [m]':>10} {'dur [s]':>8}")

    for i, (deg, dur) in enumerate(zip(melody_degrees, melody_durations), start=1):
        if deg < 0:
            # Sustained note
            note_time = dur * 2
            kind = "LONG"
            deg = -deg
        else:
            note_time = dur
            kind = "NOTE"
        samples_per_note = int(note_time * fs_song)
        # Normal note
        f_note = degree_to_freq(deg)
        L_note = freq_to_length(f_note, c=c_base)

        x, t_audio, audio, snapshots, t_snap = string_simulate(
            L=L_note,
            c=c_base,
            T=note_time,
            fs_audio=fs_song,
            N_target=N_target_song,
            ic_type="pluck",
            pluck_pos=pluck_pos_song,
            pluck_amplitude=pluck_amp_song,
            velocity_pos=parameters.velocity_pos,
            mode_number=1,          # ignored for pluck
            pickup_pos=pickup_pos_song,
            alpha=alpha_song,
        )

        seg = audio.copy()
        if len(seg) > samples_per_note:
            seg = seg[:samples_per_note]
        elif len(seg) < samples_per_note:
            seg = np.pad(seg, (0, samples_per_note - len(seg)), mode="constant")



        segments.append(seg)
        print(f"{i:4d} {str(deg):>4} {kind:>8} {f_note:12.2f} {L_note:10.3f} {note_time:8.2f}")

    song_audio = np.concatenate(segments) if segments else np.array([], dtype=float)
    print(f"\nTotal '{name}' duration: {len(song_audio)/fs_song:.2f} s")
    return song_audio



# Mary Had a Little Lamb
mary_beat = 0.5  # seconds per note

mary_degrees_with_rests = [
    3, 2, 1, 2, 3, 3, -3,     # "Mary had a little lamb" + rest
    2, 2, -2,                 # "little lamb" + rest
    3, 5, -5,                 # "little lamb" (higher) + rest
    3, 2, 1, 2, 3, 3, -3,     # "Mary had a little lamb" + rest
    2, 2, 3, 2, -1            # "its fleece was white as snow"
]

mary_durations_with_rests = [mary_beat] * len(mary_degrees_with_rests)

mary_audio_with_rests = play_melody_with_rests(
    mary_degrees_with_rests,
    mary_durations_with_rests,
    name="Mary Had a Little Lamb (pluck, longer notes, with rests)"
)

Audio(mary_audio_with_rests, rate=fs_song)


Generating 'Mary Had a Little Lamb (pluck, longer notes, with rests)' (with rests)...
Note  deg     type  f_note [Hz] L_note [m]  dur [s]
   1    3     NOTE       415.31      0.608     0.50
   2    2     NOTE       370.00      0.682     0.50
   3    1     NOTE       329.63      0.766     0.50
   4    2     NOTE       370.00      0.682     0.50
   5    3     NOTE       415.31      0.608     0.50
   6    3     NOTE       415.31      0.608     0.50
   7    3     LONG       415.31      0.608     1.00
   8    2     NOTE       370.00      0.682     0.50
   9    2     NOTE       370.00      0.682     0.50
  10    2     LONG       370.00      0.682     1.00
  11    3     NOTE       415.31      0.608     0.50
  12    5     NOTE       493.89      0.511     0.50
  13    5     LONG       493.89      0.511     1.00
  14    3     NOTE       415.31      0.608     0.50
  15    2     NOTE       370.00      0.682     0.50
  16    1     NOTE       329.63      0.766     0.50
  17    2     NOTE       370.0

In [ ]:
# Verify each note frequency via FFT

def dominant_frequency(audio, fs, fmin=50.0, fmax=None):
    """
    Estimate dominant frequency in 'audio' using a windowed one-sided FFT.
    Ignores frequencies below fmin (to avoid DC/very low junk).
    """
    eps = 1e-12
    N = len(audio)
    if N < 10:
        return np.nan

    # Remove DC and apply a Hann window to reduce leakage
    #a = audio - np.mean(audio)
    #window = np.hanning(N)
    #a_win = a * window

    Y = np.fft.rfft(audio)
    freqs = np.fft.rfftfreq(N, d=1.0/fs)
    mag = np.abs(Y) + eps

    mask = freqs >= fmin
    if fmax is not None:
        mask &= (freqs <= fmax)

    if not np.any(mask):
        return np.nan

    idxs = np.where(mask)[0]
    k = int(idxs[np.argmax(mag[idxs])])

    if k <= 0 or k >= len(mag) - 1:
        return freqs[k]

    y1 = np.log(mag[k - 1])
    y0 = np.log(mag[k])
    y2 = np.log(mag[k + 1])

    denom = (y1 - 2.0 * y0 + y2)
    if abs(denom) < eps:
        return freqs[k]

    delta = 0.5 * (y1 - y2) / denom
    delta = float(np.clip(delta, -1.0, 1.0))

    return (k + delta) * (fs / N)

print("Verifying Mary-with-rests plucked segments via FFT:\n")
print(f"{'Seg':>4} {'Deg':>4} {'type':>6} {'f_target [Hz]':>12} {'L [m]':>8} {'f_FFT [Hz]':>12} {'err [%]':>8}")

for i, (deg, dur) in enumerate(zip(mary_degrees_with_rests, mary_durations_with_rests), start=1):
    samples_per_note = int(dur * fs_song)

    if deg < 0:
        # Sustained note
        note_time = dur * 2
        kind = "LONG"
        deg = -deg
    else:
        note_time = dur
        kind = "NOTE"
    samples_per_note = int(note_time * fs_song)
    # Run plucked-string simulation
    f_note = degree_to_freq(deg)               # target frequency
    L_note = freq_to_length(f_note, c=c_base)  # string length for that f

    x, t_audio, audio, snapshots, t_snap = string_simulate(
        L=L_note,
        c=c_base,
        T=note_time,
        fs_audio=fs_song,
        N_target=N_target_song,
        ic_type="pluck",
        pluck_pos=pluck_pos_song,
        pluck_amplitude=pluck_amp_song,
        velocity_pos=parameters.velocity_pos,
        mode_number=1,               # ignored for pluck
        pickup_pos=pickup_pos_song,
        alpha=alpha_song,
    )

    seg = audio.copy()
    if len(seg) > samples_per_note:
        seg = seg[:samples_per_note]
    elif len(seg) < samples_per_note:
        seg = np.pad(seg, (0, samples_per_note - len(seg)), mode="constant")

    # FFT-based dominant frequency estimate
    f_dom = dominant_frequency(seg, fs_song, fmin=50.0)
    rel_err = 100.0 * (f_dom - f_note) / f_note if np.isfinite(f_dom) else np.nan

    print(f"{i:4d} {str(deg):>4} {kind:>6} {f_note:12.2f} {L_note:8.3f} {f_dom:12.2f} {rel_err:8.2f}")

Verifying Mary-with-rests plucked segments via FFT:

 Seg  Deg   type f_target [Hz]    L [m]   f_FFT [Hz]  err [%]
   1    3   NOTE       415.31    0.608       415.43     0.03
   2    2   NOTE       370.00    0.682       369.97    -0.01
   3    1   NOTE       329.63    0.766       329.82     0.06
   4    2   NOTE       370.00    0.682       369.97    -0.01
   5    3   NOTE       415.31    0.608       415.43     0.03
   6    3   NOTE       415.31    0.608       415.43     0.03
   7    3   LONG       415.31    0.608       415.10    -0.05
   8    2   NOTE       370.00    0.682       369.97    -0.01
   9    2   NOTE       370.00    0.682       369.97    -0.01
  10    2   LONG       370.00    0.682       369.96    -0.01
  11    3   NOTE       415.31    0.608       415.43     0.03
  12    5   NOTE       493.89    0.511       493.88    -0.00
  13    5   LONG       493.89    0.511       493.79    -0.02
  14    3   NOTE       415.31    0.608       415.43     0.03
  15    2   NOTE       370.00  

In [ ]:
# Generate per-segment videos for song

print("Generating individual videos...\n")

last_x = None  # reuse grid for rests if possible
for i, (deg, dur) in enumerate(zip(mary_degrees_with_rests, mary_durations_with_rests), start=1):
    filename = f"mary_with_rests_{i:02d}.mp4"

    if deg < 0:
            # Sustained note
            note_time = dur * 2
            kind = "LONG"
            deg = -deg
    else:
        note_time = dur
        kind = "NOTE"
    samples_per_note = int(note_time * fs_song)
    print(f"Segment {i:02d}: deg={deg}, duration={note_time:.2f} s -> {filename}")


    # Run full plucked-string simulation
    f_note = degree_to_freq(deg)
    L_note = freq_to_length(f_note, c=c_base)

    x, t_audio, audio, snapshots, t_snap = string_simulate(
        L=L_note,
        c=c_base,
        T=note_time,
        fs_audio=fs_song,
        N_target=N_target_song,
        ic_type="pluck",
        pluck_pos=pluck_pos_song,
        pluck_amplitude=pluck_amp_song,
        velocity_pos=parameters.velocity_pos,
        mode_number=1,          # ignored for pluck
        pickup_pos=pickup_pos_song,
        alpha=alpha_song,
    )

    last_x = x  # for possible following rest

    # Make the video for this segment
    string_video(
        x=x,
        snapshots=snapshots,
        t_snap=t_snap,
        audio=audio,
        fs_audio=fs_song,
        filename=filename
    )

    display(Video(filename, embed=True))

print("\nDone generating individual Mary-with-rests videos.")


Generating individual videos...

Segment 01: deg=3, duration=0.50 s -> mary_with_rests_01.mp4


Segment 02: deg=2, duration=0.50 s -> mary_with_rests_02.mp4


Segment 03: deg=1, duration=0.50 s -> mary_with_rests_03.mp4


Segment 04: deg=2, duration=0.50 s -> mary_with_rests_04.mp4


Segment 05: deg=3, duration=0.50 s -> mary_with_rests_05.mp4


...

Segment 22: deg=2, duration=0.50 s -> mary_with_rests_22.mp4


Segment 23: deg=3, duration=0.50 s -> mary_with_rests_23.mp4


Segment 24: deg=2, duration=0.50 s -> mary_with_rests_24.mp4


Segment 25: deg=1, duration=1.00 s -> mary_with_rests_25.mp4



Done generating individual Mary-with-rests videos.


In [ ]:
# Combine per-segment videos into one full video

num_segments = len(mary_degrees_with_rests)
video_clips = []

print("Loading segment videos for combination...\n")

for i in range(1, num_segments + 1):
    filename = f"mary_with_rests_{i:02d}.mp4"
    try:
        clip = VideoFileClip(filename)
        video_clips.append(clip)
        print(f"Loaded {filename}")
    except Exception as e:
        print(f"Could not load {filename}: {e}")

if not video_clips:
    print("No videos found to combine.")
else:
    print("\nConcatenating segments...")
    final_clip = concatenate_videoclips(video_clips, method="compose")

    final_name = "mary_with_rests_full.mp4"
    final_clip.write_videofile(
        final_name,
        codec="libx264",
        audio_codec="aac",
        fps=video_clips[0].fps,
        verbose=False,
        logger=None,
    )

    print(f"\nFinal combined video written to {final_name}")
    display(Video(final_name, embed=True))


Loading segment videos for combination...

Loaded mary_with_rests_01.mp4
Loaded mary_with_rests_02.mp4
Loaded mary_with_rests_03.mp4
Loaded mary_with_rests_04.mp4
Loaded mary_with_rests_05.mp4
Loaded mary_with_rests_06.mp4
Loaded mary_with_rests_07.mp4
Loaded mary_with_rests_08.mp4
Loaded mary_with_rests_09.mp4
Loaded mary_with_rests_10.mp4
Loaded mary_with_rests_11.mp4
Loaded mary_with_rests_12.mp4
Loaded mary_with_rests_13.mp4
Loaded mary_with_rests_14.mp4
Loaded mary_with_rests_15.mp4
Loaded mary_with_rests_16.mp4
Loaded mary_with_rests_17.mp4
Loaded mary_with_rests_18.mp4
Loaded mary_with_rests_19.mp4
Loaded mary_with_rests_20.mp4
Loaded mary_with_rests_21.mp4
Loaded mary_with_rests_22.mp4
Loaded mary_with_rests_23.mp4
Loaded mary_with_rests_24.mp4
Loaded mary_with_rests_25.mp4

Concatenating segments...

Final combined video written to mary_with_rests_full.mp4


In [ ]:
# Twinkle Twinkle
beat = 0.35

# Phrase (no rests): 1 1 5 5 6 6 5 etc.
phrase1 = [1, 1, 5, 5, 6, 6, -5]
phrase2 = [4, 4, 3, 3, 2, 2, -1]
phrase3 = [5, 5, 4, 4, 3, 3, -2]
phrase4 = phrase3
phrase5 = phrase1
phrase6 = phrase2

twinkle_degrees_rests = phrase1 + phrase2 + phrase3 + phrase4 + phrase5 + phrase6


twinkle_durations_rests = [beat] * len(twinkle_degrees_rests)  # rest is same length as a note

twinkle_audio_rests = play_melody_with_rests(
    twinkle_degrees_rests,
    twinkle_durations_rests,
    name="Twinkle Twinkle (pluck, one string, with rests)"
)

Audio(twinkle_audio_rests, rate=fs_song)


Generating 'Twinkle Twinkle (pluck, one string, with rests)' (with rests)...
Note  deg     type  f_note [Hz] L_note [m]  dur [s]
   1    1     NOTE       329.63      0.766     0.35
   2    1     NOTE       329.63      0.766     0.35
   3    5     NOTE       493.89      0.511     0.35
   4    5     NOTE       493.89      0.511     0.35
   5    6     NOTE       554.37      0.455     0.35
   6    6     NOTE       554.37      0.455     0.35
   7    5     LONG       493.89      0.511     0.70
   8    4     NOTE       440.00      0.574     0.35
   9    4     NOTE       440.00      0.574     0.35
  10    3     NOTE       415.31      0.608     0.35
  11    3     NOTE       415.31      0.608     0.35
  12    2     NOTE       370.00      0.682     0.35
  13    2     NOTE       370.00      0.682     0.35
  14    1     LONG       329.63      0.766     0.70
  15    5     NOTE       493.89      0.511     0.35
  16    5     NOTE       493.89      0.511     0.35
  17    4     NOTE       440.00      0.

In [ ]:
# Verify each note frequency via FFT

def dominant_frequency(audio, fs, fmin=50.0, fmax=None):
    """
    Estimate dominant frequency in 'audio' using a windowed one-sided FFT.
    Ignores frequencies below fmin (to avoid DC/very low junk).
    """
    eps = 1e-12
    N = len(audio)
    if N < 10:
        return np.nan

    # Remove DC and apply a Hann window to reduce leakage
    #a = audio - np.mean(audio)
    #window = np.hanning(N)
    #a_win = a * window

    Y = np.fft.rfft(audio)
    freqs = np.fft.rfftfreq(N, d=1.0/fs)
    mag = np.abs(Y) + eps

    mask = freqs >= fmin
    if fmax is not None:
        mask &= (freqs <= fmax)

    if not np.any(mask):
        return np.nan

    idxs = np.where(mask)[0]
    k = int(idxs[np.argmax(mag[idxs])])

    if k <= 0 or k >= len(mag) - 1:
        return freqs[k]

    y1 = np.log(mag[k - 1])
    y0 = np.log(mag[k])
    y2 = np.log(mag[k + 1])

    denom = (y1 - 2.0 * y0 + y2)
    if abs(denom) < eps:
        return freqs[k]

    delta = 0.5 * (y1 - y2) / denom
    delta = float(np.clip(delta, -1.0, 1.0))

    return (k + delta) * (fs / N)

print("Verifying Mary-with-rests plucked segments via FFT:\n")
print(f"{'Seg':>4} {'Deg':>4} {'type':>6} {'f_target [Hz]':>12} {'L [m]':>8} {'f_FFT [Hz]':>12} {'err [%]':>8}")

for i, (deg, dur) in enumerate(zip(mary_degrees_with_rests, mary_durations_with_rests), start=1):
    samples_per_note = int(dur * fs_song)

    if deg < 0:
        # Sustained note
        note_time = dur * 2
        kind = "LONG"
        deg = -deg
    else:
        note_time = dur
        kind = "NOTE"
    samples_per_note = int(note_time * fs_song)
    # Run plucked-string simulation
    f_note = degree_to_freq(deg)               # target frequency
    L_note = freq_to_length(f_note, c=c_base)  # string length for that f

    x, t_audio, audio, snapshots, t_snap = string_simulate(
        L=L_note,
        c=c_base,
        T=note_time,
        fs_audio=fs_song,
        N_target=N_target_song,
        ic_type="pluck",
        pluck_pos=pluck_pos_song,
        pluck_amplitude=pluck_amp_song,
        velocity_pos=parameters.velocity_pos,
        mode_number=1,               # ignored for pluck
        pickup_pos=pickup_pos_song,
        alpha=alpha_song,
    )

    seg = audio.copy()
    if len(seg) > samples_per_note:
        seg = seg[:samples_per_note]
    elif len(seg) < samples_per_note:
        seg = np.pad(seg, (0, samples_per_note - len(seg)), mode="constant")

    # FFT-based dominant frequency estimate
    f_dom = dominant_frequency(seg, fs_song, fmin=50.0)
    rel_err = 100.0 * (f_dom - f_note) / f_note if np.isfinite(f_dom) else np.nan

    print(f"{i:4d} {str(deg):>4} {kind:>6} {f_note:12.2f} {L_note:8.3f} {f_dom:12.2f} {rel_err:8.2f}")

Verifying Mary-with-rests plucked segments via FFT:

 Seg  Deg   type f_target [Hz]    L [m]   f_FFT [Hz]  err [%]
   1    3   NOTE       415.31    0.608       415.43     0.03
   2    2   NOTE       370.00    0.682       369.97    -0.01
   3    1   NOTE       329.63    0.766       329.82     0.06
   4    2   NOTE       370.00    0.682       369.97    -0.01
   5    3   NOTE       415.31    0.608       415.43     0.03
   6    3   NOTE       415.31    0.608       415.43     0.03
   7    3   LONG       415.31    0.608       415.10    -0.05
   8    2   NOTE       370.00    0.682       369.97    -0.01
   9    2   NOTE       370.00    0.682       369.97    -0.01
  10    2   LONG       370.00    0.682       369.96    -0.01
  11    3   NOTE       415.31    0.608       415.43     0.03
  12    5   NOTE       493.89    0.511       493.88    -0.00
  13    5   LONG       493.89    0.511       493.79    -0.02
  14    3   NOTE       415.31    0.608       415.43     0.03
  15    2   NOTE       370.00  

In [ ]:
# Generate per-segment videos
print("Generating Twinkle-with-rests segment videos...\n")

last_x = None  # reuse a grid for rests

for i, (deg, dur) in enumerate(zip(twinkle_degrees_rests, twinkle_durations_rests), start=1):
    filename = f"twinkle_with_rests_{i:02d}.mp4"
    if deg < 0:
        # Sustained note
        note_time = dur * 2
        kind = "LONG"
        deg = -deg
    else:
        note_time = dur
        kind = "NOTE"
    samples_per_note = int(note_time * fs_song)
    print(f"Segment {i:02d}: deg={deg}, duration={note_time:.2f} s -> {filename}")


    # Run full plucked-string simulation
    f_note = degree_to_freq(deg)
    L_note = freq_to_length(f_note, c=c_base)

    x, t_audio, audio, snapshots, t_snap = string_simulate(
        L=L_note,
        c=c_base,
        T=note_time,
        fs_audio=fs_song,
        N_target=N_target_song,
        ic_type="pluck",
        pluck_pos=pluck_pos_song,
        pluck_amplitude=pluck_amp_song,
        velocity_pos=parameters.velocity_pos,
        mode_number=1,          # ignored for pluck
        pickup_pos=pickup_pos_song,
        alpha=alpha_song,
    )

    last_x = x  # for possible following rest

    # Make the video for this segment
    string_video(
        x=x,
        snapshots=snapshots,
        t_snap=t_snap,
        audio=audio,
        fs_audio=fs_song,
        filename=filename
    )

    display(Video(filename, embed=True))

print("\nDone generating Twinkle-with-rests segment videos.")


Generating Twinkle-with-rests segment videos...

Segment 01: deg=1, duration=0.35 s -> twinkle_with_rests_01.mp4


Segment 02: deg=1, duration=0.35 s -> twinkle_with_rests_02.mp4


Segment 03: deg=5, duration=0.35 s -> twinkle_with_rests_03.mp4


Segment 04: deg=5, duration=0.35 s -> twinkle_with_rests_04.mp4


Segment 05: deg=6, duration=0.35 s -> twinkle_with_rests_05.mp4


...

Segment 39: deg=3, duration=0.35 s -> twinkle_with_rests_39.mp4


Segment 40: deg=2, duration=0.35 s -> twinkle_with_rests_40.mp4


Segment 41: deg=2, duration=0.35 s -> twinkle_with_rests_41.mp4


Segment 42: deg=1, duration=0.70 s -> twinkle_with_rests_42.mp4



Done generating Twinkle-with-rests segment videos.


In [ ]:
# Combine segment videos into one full video

num_twinkle_segments = len(twinkle_degrees_rests)
video_clips = []

print("Loading Twinkle-with-rests segment videos for combination...\n")

for i in range(1, num_twinkle_segments + 1):
    filename = f"twinkle_with_rests_{i:02d}.mp4"
    try:
        clip = VideoFileClip(filename)
        video_clips.append(clip)
        print(f"Loaded {filename}")
    except Exception as e:
        print(f"Could not load {filename}: {e}")

if not video_clips:
    print("No Twinkle-with-rests videos found to combine.")
else:
    print("\nConcatenating Twinkle-with-rests segments...")
    final_clip = concatenate_videoclips(video_clips, method="compose")

    final_name = "twinkle_with_rests_full.mp4"
    final_clip.write_videofile(
        final_name,
        codec="libx264",
        audio_codec="aac",
        fps=video_clips[0].fps,
        verbose=False,
        logger=None,
    )

    print(f"\nFinal Twinkle-with-rests combined video written to {final_name}")
    display(Video(final_name, embed=True))


Loading Twinkle-with-rests segment videos for combination...

Loaded twinkle_with_rests_01.mp4
Loaded twinkle_with_rests_02.mp4
Loaded twinkle_with_rests_03.mp4
Loaded twinkle_with_rests_04.mp4
Loaded twinkle_with_rests_05.mp4
Loaded twinkle_with_rests_06.mp4
Loaded twinkle_with_rests_07.mp4
Loaded twinkle_with_rests_08.mp4
Loaded twinkle_with_rests_09.mp4
Loaded twinkle_with_rests_10.mp4
Loaded twinkle_with_rests_11.mp4
Loaded twinkle_with_rests_12.mp4
Loaded twinkle_with_rests_13.mp4
Loaded twinkle_with_rests_14.mp4
Loaded twinkle_with_rests_15.mp4
Loaded twinkle_with_rests_16.mp4
Loaded twinkle_with_rests_17.mp4
Loaded twinkle_with_rests_18.mp4
Loaded twinkle_with_rests_19.mp4
Loaded twinkle_with_rests_20.mp4
Loaded twinkle_with_rests_21.mp4
Loaded twinkle_with_rests_22.mp4
Loaded twinkle_with_rests_23.mp4
Loaded twinkle_with_rests_24.mp4
Loaded twinkle_with_rests_25.mp4
Loaded twinkle_with_rests_26.mp4
Loaded twinkle_with_rests_27.mp4
Loaded twinkle_with_rests_28.mp4
Loaded twinkle